In [1]:
import sys
import numpy as np
import scipy.sparse as sp
from keras import backend as K
from keras.models import Model
from keras import initializers
from keras.regularizers import l2
from keras.optimizers import Adam, SGD
from keras.layers import Embedding, Input, merge, Flatten, concatenate, multiply, Dense
from evaluate import evaluate_model
import GMF, MLP

Using TensorFlow backend.
/home/natu/.local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:523: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/natu/.local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:524: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/natu/.local/lib/python3.6/site-packages/tensorflow/python/framework/dtypes.py:525: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/natu/.local/lib/python3.6/site-packages/tensorflow/python/framewo

In [2]:
num_epochs = 100
batch_size = 128
mf_dim = 8
layers = [64, 32, 16, 8]
reg_mf = 0
reg_layers = [0, 0, 0, 0]
num_negatives = 4
learning_rate = 0.001
learner = Adam
verbose = 0
# mf_pretrain = args.mf_pretrain
# mlp_pretrain = args.mlp_pretrain
topK = 10
num_layer = len(layers)
evaluation_threads = 1
model_out_file = 'Pretrain/%s_NeuMF_%d_%s.h5' %('NCF', mf_dim, layers)

In [3]:
# Read training data
num_users, num_items = 0, 0
with open('Data/ml-1m.train.rating', "r") as f:
    line = f.readline()
    while line != None and line != "":
        arr = line.split("\t")
        u, i = int(arr[0]), int(arr[1])
        num_users = max(num_users, u)
        num_items = max(num_items, i)
        line = f.readline()
print(num_users)
print(num_items)

6039
3705


In [4]:
mat = sp.dok_matrix((num_users+1, num_items+1), dtype=np.float32)
print(mat.todense())
print(mat.todense().shape)
with open('Data/ml-1m.train.rating', "r") as f:
    line = f.readline()
    while line != None and line != "":
        arr = line.split("\t")
        user, item, rating = int(arr[0]), int(arr[1]), float(arr[2])
        if (rating > 0):
            mat[user, item] = 1.0
        line = f.readline()   
mat.todense() # matrix if user rating item = 1

[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
(6040, 3706)


matrix([[1., 1., 1., ..., 0., 0., 0.],
        [1., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 1., 1., ..., 0., 0., 0.],
        [1., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [5]:
# Read test data
ratingList = []
with open("Data/ml-1m.test.rating", "r") as f:
    line = f.readline()
    while line != None and line != "":
        arr = line.split("\t")
        user, item = int(arr[0]), int(arr[1])
        ratingList.append([user, item])
        line = f.readline()
print(len(ratingList))
ratingList

6040


[[0, 25],
 [1, 133],
 [2, 207],
 [3, 208],
 [4, 222],
 [5, 396],
 [6, 74],
 [7, 91],
 [8, 514],
 [9, 659],
 [10, 820],
 [11, 829],
 [12, 844],
 [13, 105],
 [14, 519],
 [15, 218],
 [16, 246],
 [17, 228],
 [18, 770],
 [19, 641],
 [20, 1167],
 [21, 1195],
 [22, 934],
 [23, 603],
 [24, 872],
 [25, 352],
 [26, 839],
 [27, 1299],
 [28, 1458],
 [29, 1487],
 [30, 274],
 [31, 1521],
 [32, 459],
 [33, 91],
 [34, 1647],
 [35, 1071],
 [36, 808],
 [37, 244],
 [38, 237],
 [39, 1696],
 [40, 303],
 [41, 730],
 [42, 104],
 [43, 472],
 [44, 1772],
 [45, 1805],
 [46, 1624],
 [47, 360],
 [48, 968],
 [49, 1879],
 [50, 1595],
 [51, 788],
 [52, 245],
 [53, 1236],
 [54, 171],
 [55, 534],
 [56, 7],
 [57, 1719],
 [58, 170],
 [59, 488],
 [60, 2063],
 [61, 2119],
 [62, 743],
 [63, 876],
 [64, 693],
 [65, 41],
 [66, 82],
 [67, 19],
 [68, 485],
 [69, 237],
 [70, 317],
 [71, 18],
 [72, 1148],
 [73, 1646],
 [74, 939],
 [75, 267],
 [76, 445],
 [77, 1459],
 [78, 73],
 [79, 123],
 [80, 44],
 [81, 991],
 [82, 1904],
 [83

In [6]:
# Read negative data
negativeList = []
with open("Data/ml-1m.test.negative", "r") as f:
    line = f.readline()
    while line != None and line != "":
        arr = line.split("\t")
        negatives = []
        for x in arr[1: ]:
            negatives.append(int(x))
        negativeList.append(negatives)
        line = f.readline()
print(len(negativeList))
negativeList

6040


[[1064,
  174,
  2791,
  3373,
  269,
  2678,
  1902,
  3641,
  1216,
  915,
  3672,
  2803,
  2344,
  986,
  3217,
  2824,
  2598,
  464,
  2340,
  1952,
  1855,
  1353,
  1547,
  3487,
  3293,
  1541,
  2414,
  2728,
  340,
  1421,
  1963,
  2545,
  972,
  487,
  3463,
  2727,
  1135,
  3135,
  128,
  175,
  2423,
  1974,
  2515,
  3278,
  3079,
  1527,
  2182,
  1018,
  2800,
  1830,
  1539,
  617,
  247,
  3448,
  1699,
  1420,
  2487,
  198,
  811,
  1010,
  1423,
  2840,
  1770,
  881,
  1913,
  1803,
  1734,
  3326,
  1617,
  224,
  3352,
  1869,
  1182,
  1331,
  336,
  2517,
  1721,
  3512,
  3656,
  273,
  1026,
  1991,
  2190,
  998,
  3386,
  3369,
  185,
  2822,
  864,
  2854,
  3067,
  58,
  2551,
  2333,
  2688,
  3703,
  1300,
  1924,
  3118],
 [1072,
  3154,
  3368,
  3644,
  549,
  1810,
  937,
  1514,
  1713,
  2186,
  660,
  2303,
  2416,
  670,
  1176,
  788,
  889,
  3120,
  2344,
  2525,
  3301,
  2055,
  1436,
  2630,
  11,
  2773,
  2176,
  1847,
  740,
  2332,

In [7]:
train, testRatings, testNegatives = mat, ratingList, negativeList
num_users, num_items = train.shape

In [8]:
def init_normal(shape):
    return K.random_normal(shape, dtype= 'float32')

In [9]:
# Get model
user_input = Input(shape=(1,), dtype='int64', name = 'user_input')
item_input = Input(shape=(1,), dtype='int64', name = 'item_input')
MF_Embedding_User = Embedding(input_dim = num_users, output_dim = mf_dim, name = 'mf_embedding_user',
                              embeddings_initializer = init_normal, embeddings_regularizer = l2(reg_mf), input_length=1)
MF_Embedding_Item = Embedding(input_dim = num_items, output_dim = mf_dim, name = 'mf_embedding_item',
                              embeddings_initializer = init_normal, embeddings_regularizer = l2(reg_mf), input_length=1) 
MLP_Embedding_User = Embedding(input_dim = num_users, output_dim = int(layers[0]/2), name = "mlp_embedding_user",
                              embeddings_initializer = init_normal, embeddings_regularizer = l2(reg_layers[0]), input_length=1)
MLP_Embedding_Item = Embedding(input_dim = num_items, output_dim = int(layers[0]/2), name = 'mlp_embedding_item',
                              embeddings_initializer = init_normal, embeddings_regularizer = l2(reg_layers[0]), input_length=1) 
mf_user_latent = Flatten()(MF_Embedding_User(user_input))
mf_item_latent = Flatten()(MF_Embedding_Item(item_input))
#
mlp_user_latent = Flatten()(MLP_Embedding_User(user_input))
mlp_item_latent = Flatten()(MLP_Embedding_Item(item_input))
mlp_vector = concatenate([mlp_user_latent, mlp_item_latent])
mf_vector = multiply([mf_user_latent, mf_item_latent]) # element-wise multiply
for idx in range(1, num_layer):
    layer = Dense(layers[idx], activity_regularizer= l2(reg_layers[idx]), activation='relu', name="layer%d" %idx)
    mlp_vector = layer(mlp_vector)
predict_vector = concatenate([mf_vector, mlp_vector])
prediction = Dense(1, activation='sigmoid', kernel_initializer='lecun_uniform', name = "prediction")(predict_vector)
model = Model(inputs=[user_input, item_input], outputs= prediction)
model.compile(optimizer=Adam(lr=learning_rate), loss='binary_crossentropy', metrics= ['accuracy'])

In [10]:
# Training
def get_train_instances(train, num_negatives):
    user_input, item_input, labels = [],[],[]
    num_users = train.shape[0]
    for (u, i) in train.keys():
        # positive instance
        user_input.append(u)
        item_input.append(i)
        labels.append(1)
        # negative instances
        for t in range(num_negatives):
            j = np.random.randint(num_items)
            while (u, j) in train:
                j = np.random.randint(num_items)
            user_input.append(u)
            item_input.append(j)
            labels.append(0)
    return user_input, item_input, labels
user_input_data, item_input_data, labels_data = get_train_instances(train, num_negatives)
print(len(user_input_data))
print(len(item_input_data))
print(len(labels_data))

4970845
4970845
4970845


In [11]:
[np.array(user_input_data), np.array(item_input_data)]

[array([   0,    0,    0, ..., 6039, 6039, 6039]),
 array([  32,  844, 2486, ..., 2165,  836, 1761])]

In [12]:
best_hr = 0
for epoch in range(num_epochs):
    # Fit model
    user_input_data, item_input_data, labels_data = get_train_instances(train, num_negatives)
    hist = model.fit([np.array(user_input_data), np.array(item_input_data)], #input
                    np.array(labels_data), # labels 
                    batch_size=batch_size, epochs=1, shuffle=True)
    # Evaluate model
    if epoch % 10 == 0:
        (hits, ndcgs) = evaluate_model(model, testRatings, testNegatives, topK, evaluation_threads)
        hr, ndcg, loss = np.array(hits).mean(), np.array(ndcgs).mean(), hist.history['loss'][0]
        print('Iteration %d : HR = %.4f, NDCG = %.4f, loss = %.4f' % (epoch, hr, ndcg, loss))
        if hr > best_hr:           
            best_hr, best_ndcg, best_iter = hr, ndcg, epoch
            model.save_weights(model_out_file, overwrite=True)

In [13]:
# model.load_weights('Pretrain/NCF_NeuMF_8_[64, 32, 16, 8].h5')

In [15]:
# (hits, ndcgs) = evaluate_model(model, testRatings, testNegatives, topK, evaluation_threads)

[0, 25]
[1064, 174, 2791, 3373, 269, 2678, 1902, 3641, 1216, 915, 3672, 2803, 2344, 986, 3217, 2824, 2598, 464, 2340, 1952, 1855, 1353, 1547, 3487, 3293, 1541, 2414, 2728, 340, 1421, 1963, 2545, 972, 487, 3463, 2727, 1135, 3135, 128, 175, 2423, 1974, 2515, 3278, 3079, 1527, 2182, 1018, 2800, 1830, 1539, 617, 247, 3448, 1699, 1420, 2487, 198, 811, 1010, 1423, 2840, 1770, 881, 1913, 1803, 1734, 3326, 1617, 224, 3352, 1869, 1182, 1331, 336, 2517, 1721, 3512, 3656, 273, 1026, 1991, 2190, 998, 3386, 3369, 185, 2822, 864, 2854, 3067, 58, 2551, 2333, 2688, 3703, 1300, 1924, 3118]
[1064, 174, 2791, 3373, 269, 2678, 1902, 3641, 1216, 915, 3672, 2803, 2344, 986, 3217, 2824, 2598, 464, 2340, 1952, 1855, 1353, 1547, 3487, 3293, 1541, 2414, 2728, 340, 1421, 1963, 2545, 972, 487, 3463, 2727, 1135, 3135, 128, 175, 2423, 1974, 2515, 3278, 3079, 1527, 2182, 1018, 2800, 1830, 1539, 617, 247, 3448, 1699, 1420, 2487, 198, 811, 1010, 1423, 2840, 1770, 881, 1913, 1803, 1734, 3326, 1617, 224, 3352, 1869, 118

[164, 864]
[3282, 368, 1914, 1623, 997, 10, 786, 2923, 2438, 3311, 270, 2016, 764, 3396, 2329, 2620, 2236, 1667, 2540, 2786, 1988, 2845, 195, 792, 899, 3310, 982, 788, 1460, 3450, 2875, 3604, 1614, 2094, 3635, 3593, 3399, 520, 566, 208, 1402, 402, 3188, 2227, 2767, 578, 1692, 430, 250, 1534, 3191, 1551, 893, 2068, 2823, 3619, 2950, 3151, 2472, 3084, 1044, 2014, 3503, 3513, 1436, 1145, 1059, 3031, 2274, 1876, 2682, 1650, 257, 2825, 2427, 39, 3617, 2614, 2365, 1052, 2008, 1910, 627, 3367, 2566, 3561, 2212, 2411, 620, 314, 2918, 3515, 452, 2442, 2970, 2752, 1877, 3272, 685]
[3282, 368, 1914, 1623, 997, 10, 786, 2923, 2438, 3311, 270, 2016, 764, 3396, 2329, 2620, 2236, 1667, 2540, 2786, 1988, 2845, 195, 792, 899, 3310, 982, 788, 1460, 3450, 2875, 3604, 1614, 2094, 3635, 3593, 3399, 520, 566, 208, 1402, 402, 3188, 2227, 2767, 578, 1692, 430, 250, 1534, 3191, 1551, 893, 2068, 2823, 3619, 2950, 3151, 2472, 3084, 1044, 2014, 3503, 3513, 1436, 1145, 1059, 3031, 2274, 1876, 2682, 1650, 257, 2825

[307, 1858]
[1235, 3176, 1560, 2928, 309, 2151, 1472, 655, 2993, 1485, 2358, 1778, 1064, 2521, 821, 828, 2853, 2430, 2915, 2550, 3143, 705, 2297, 1264, 2622, 1224, 2816, 683, 3094, 1804, 2289, 2885, 2303, 2450, 704, 3014, 2901, 402, 1929, 3139, 2589, 3509, 1320, 2775, 1892, 289, 480, 339, 3439, 2663, 3106, 917, 1305, 2963, 3258, 2412, 1972, 181, 3673, 2287, 3374, 1516, 1541, 1342, 2182, 1187, 416, 3003, 3615, 3018, 2421, 2712, 980, 1041, 3230, 3340, 1243, 3631, 3153, 3352, 2875, 491, 1709, 777, 1374, 2294, 2883, 2567, 378, 2766, 2734, 545, 1739, 3388, 3062, 2890, 451, 650, 3632]
[1235, 3176, 1560, 2928, 309, 2151, 1472, 655, 2993, 1485, 2358, 1778, 1064, 2521, 821, 828, 2853, 2430, 2915, 2550, 3143, 705, 2297, 1264, 2622, 1224, 2816, 683, 3094, 1804, 2289, 2885, 2303, 2450, 704, 3014, 2901, 402, 1929, 3139, 2589, 3509, 1320, 2775, 1892, 289, 480, 339, 3439, 2663, 3106, 917, 1305, 2963, 3258, 2412, 1972, 181, 3673, 2287, 3374, 1516, 1541, 1342, 2182, 1187, 416, 3003, 3615, 3018, 2421, 2

[461, 340]
[83, 1112, 1194, 1528, 1625, 1895, 887, 1081, 3425, 2176, 527, 3437, 2608, 2511, 1550, 1149, 1527, 2702, 3605, 889, 1273, 1079, 1467, 284, 2886, 3682, 1839, 3134, 1144, 407, 2153, 2475, 111, 3693, 2529, 3463, 2468, 226, 2942, 1788, 1589, 3447, 2850, 1220, 3429, 2556, 2791, 2403, 2209, 488, 1070, 1228, 1427, 3387, 2193, 2591, 863, 3676, 3094, 2097, 3262, 2317, 1322, 3607, 406, 3022, 2145, 1850, 1452, 508, 2697, 2406, 3228, 1967, 946, 1543, 573, 2332, 2350, 307, 2496, 750, 95, 1488, 2852, 1459, 3250, 2181, 1674, 1360, 1588, 361, 3545, 1831, 2586, 795, 3183, 2639, 3159]
[83, 1112, 1194, 1528, 1625, 1895, 887, 1081, 3425, 2176, 527, 3437, 2608, 2511, 1550, 1149, 1527, 2702, 3605, 889, 1273, 1079, 1467, 284, 2886, 3682, 1839, 3134, 1144, 407, 2153, 2475, 111, 3693, 2529, 3463, 2468, 226, 2942, 1788, 1589, 3447, 2850, 1220, 3429, 2556, 2791, 2403, 2209, 488, 1070, 1228, 1427, 3387, 2193, 2591, 863, 3676, 3094, 2097, 3262, 2317, 1322, 3607, 406, 3022, 2145, 1850, 1452, 508, 2697, 2

[614, 134]
[2472, 453, 1410, 2910, 1843, 542, 3549, 354, 2634, 1742, 3576, 2103, 3461, 3309, 1082, 286, 1769, 3030, 218, 809, 1207, 2727, 140, 615, 1013, 426, 1460, 2029, 1462, 1947, 3248, 2666, 845, 1733, 1136, 1353, 2547, 3614, 25, 3421, 1190, 211, 3407, 2956, 822, 3567, 366, 2135, 2717, 3008, 3191, 2793, 659, 2987, 3679, 3281, 2065, 2578, 1317, 1638, 1250, 3138, 3122, 214, 1408, 786, 2378, 309, 1702, 1314, 105, 2294, 503, 1896, 2522, 2323, 1527, 2099, 3075, 1015, 3338, 1581, 1306, 908, 2033, 2431, 2232, 3426, 1713, 133, 3382, 795, 1857, 2176, 1087, 3077, 2061, 1066, 1540]
[2472, 453, 1410, 2910, 1843, 542, 3549, 354, 2634, 1742, 3576, 2103, 3461, 3309, 1082, 286, 1769, 3030, 218, 809, 1207, 2727, 140, 615, 1013, 426, 1460, 2029, 1462, 1947, 3248, 2666, 845, 1733, 1136, 1353, 2547, 3614, 25, 3421, 1190, 211, 3407, 2956, 822, 3567, 366, 2135, 2717, 3008, 3191, 2793, 659, 2987, 3679, 3281, 2065, 2578, 1317, 1638, 1250, 3138, 3122, 214, 1408, 786, 2378, 309, 1702, 1314, 105, 2294, 503, 

...

[5476, 1613]
[2605, 1937, 598, 2550, 28, 2435, 1853, 1924, 851, 3276, 2647, 657, 1045, 3664, 2112, 2447, 701, 1623, 1907, 2800, 862, 2608, 3068, 3053, 3389, 1797, 1434, 3374, 1716, 3690, 780, 1378, 2557, 703, 1188, 241, 3247, 1456, 3242, 2528, 1073, 2199, 2090, 3284, 1538, 1030, 908, 1903, 836, 3455, 3232, 1292, 1911, 2978, 2240, 1561, 2984, 1044, 74, 3550, 2326, 87, 1878, 2674, 346, 2818, 1601, 2505, 2838, 539, 2673, 740, 3526, 260, 614, 17, 1410, 885, 2477, 2549, 3536, 905, 2696, 1405, 2599, 1015, 3604, 2410, 2950, 2093, 3279, 2222, 1824, 2606, 218, 3402, 897, 3484, 3227]
[2605, 1937, 598, 2550, 28, 2435, 1853, 1924, 851, 3276, 2647, 657, 1045, 3664, 2112, 2447, 701, 1623, 1907, 2800, 862, 2608, 3068, 3053, 3389, 1797, 1434, 3374, 1716, 3690, 780, 1378, 2557, 703, 1188, 241, 3247, 1456, 3242, 2528, 1073, 2199, 2090, 3284, 1538, 1030, 908, 1903, 836, 3455, 3232, 1292, 1911, 2978, 2240, 1561, 2984, 1044, 74, 3550, 2326, 87, 1878, 2674, 346, 2818, 1601, 2505, 2838, 539, 2673, 740, 3526,

[5577, 1145]
[2633, 395, 2080, 1596, 1481, 2748, 3001, 2647, 2772, 2966, 347, 138, 3522, 248, 2598, 2210, 1298, 3686, 3094, 2233, 2621, 2309, 3050, 2453, 3249, 1600, 1242, 446, 3453, 70, 3421, 3620, 2240, 3307, 3695, 3321, 2943, 2545, 229, 849, 674, 2614, 1871, 1274, 2407, 370, 1088, 1942, 947, 2574, 2021, 2496, 653, 3640, 2588, 1991, 3588, 2530, 938, 2550, 162, 3557, 1038, 784, 3172, 2140, 918, 962, 1070, 3458, 3424, 213, 2678, 1024, 1223, 831, 1373, 1049, 3437, 298, 1920, 582, 980, 1010, 2670, 879, 2471, 3067, 3079, 557, 2007, 216, 3400, 3671, 2875, 2270, 1081, 3112, 3510]
[2633, 395, 2080, 1596, 1481, 2748, 3001, 2647, 2772, 2966, 347, 138, 3522, 248, 2598, 2210, 1298, 3686, 3094, 2233, 2621, 2309, 3050, 2453, 3249, 1600, 1242, 446, 3453, 70, 3421, 3620, 2240, 3307, 3695, 3321, 2943, 2545, 229, 849, 674, 2614, 1871, 1274, 2407, 370, 1088, 1942, 947, 2574, 2021, 2496, 653, 3640, 2588, 1991, 3588, 2530, 938, 2550, 162, 3557, 1038, 784, 3172, 2140, 918, 962, 1070, 3458, 3424, 213, 2678

[5696, 864]
[3007, 1925, 3216, 2022, 2313, 2973, 2482, 2542, 214, 2348, 1967, 2101, 3108, 1870, 3462, 2408, 2231, 3393, 1453, 2036, 3406, 2727, 3332, 3257, 1511, 2366, 3539, 3054, 1156, 3136, 3289, 1829, 3245, 260, 3643, 2094, 701, 2769, 396, 913, 428, 3654, 2699, 2102, 1802, 3195, 2996, 1890, 2885, 3026, 1039, 3519, 1330, 457, 2532, 883, 1169, 199, 3272, 3670, 81, 480, 1163, 367, 129, 2318, 3649, 3438, 3589, 2793, 3183, 2584, 3420, 976, 3521, 1650, 764, 1926, 3518, 1694, 2888, 716, 1901, 2871, 1274, 3065, 1809, 1610, 3260, 3107, 1913, 2503, 242, 903, 387, 3372, 1183, 1382, 1564]
[3007, 1925, 3216, 2022, 2313, 2973, 2482, 2542, 214, 2348, 1967, 2101, 3108, 1870, 3462, 2408, 2231, 3393, 1453, 2036, 3406, 2727, 3332, 3257, 1511, 2366, 3539, 3054, 1156, 3136, 3289, 1829, 3245, 260, 3643, 2094, 701, 2769, 396, 913, 428, 3654, 2699, 2102, 1802, 3195, 2996, 1890, 2885, 3026, 1039, 3519, 1330, 457, 2532, 883, 1169, 199, 3272, 3670, 81, 480, 1163, 367, 129, 2318, 3649, 3438, 3589, 2793, 3183, 

[5805, 297]
[1386, 791, 3226, 3148, 383, 403, 545, 3459, 2586, 161, 1344, 3529, 3308, 522, 3604, 619, 2589, 3685, 1575, 571, 1783, 788, 3677, 964, 1561, 2649, 1679, 418, 806, 556, 158, 2323, 930, 348, 2385, 2575, 552, 1149, 2426, 2135, 2714, 3379, 223, 748, 2494, 3076, 1548, 2906, 557, 235, 1302, 2196, 1798, 2118, 3511, 471, 1864, 2428, 1264, 1574, 1212, 1414, 1633, 638, 1648, 56, 3361, 2261, 1863, 2445, 456, 2997, 3415, 3614, 2006, 325, 34, 1485, 1087, 2878, 600, 2115, 921, 1916, 2550, 1366, 3302, 1308, 881, 85, 632, 2025, 2255, 2819, 2308, 3320, 2325, 193, 790]
[1386, 791, 3226, 3148, 383, 403, 545, 3459, 2586, 161, 1344, 3529, 3308, 522, 3604, 619, 2589, 3685, 1575, 571, 1783, 788, 3677, 964, 1561, 2649, 1679, 418, 806, 556, 158, 2323, 930, 348, 2385, 2575, 552, 1149, 2426, 2135, 2714, 3379, 223, 748, 2494, 3076, 1548, 2906, 557, 235, 1302, 2196, 1798, 2118, 3511, 471, 1864, 2428, 1264, 1574, 1212, 1414, 1633, 638, 1648, 56, 3361, 2261, 1863, 2445, 456, 2997, 3415, 3614, 2006, 325, 

[5948, 2450]
[1156, 605, 1696, 1308, 1490, 751, 3139, 3335, 1445, 2822, 785, 2672, 3629, 378, 2368, 1044, 2499, 2826, 393, 1169, 2696, 3508, 1665, 2098, 1419, 2001, 271, 1465, 3308, 1127, 2270, 182, 3674, 2831, 2318, 2716, 1776, 3368, 2981, 2986, 362, 561, 2228, 636, 830, 3216, 1947, 249, 3035, 1714, 3520, 1132, 3301, 1908, 2130, 3197, 2967, 2154, 1074, 1671, 2085, 3671, 813, 415, 2294, 613, 326, 1719, 923, 1505, 3445, 1256, 2905, 2589, 3584, 1670, 1140, 2931, 3344, 2349, 1499, 2263, 2661, 972, 196, 1881, 56, 2853, 3450, 266, 2289, 1217, 3008, 2546, 3143, 2745, 2347, 3170, 2805]
[1156, 605, 1696, 1308, 1490, 751, 3139, 3335, 1445, 2822, 785, 2672, 3629, 378, 2368, 1044, 2499, 2826, 393, 1169, 2696, 3508, 1665, 2098, 1419, 2001, 271, 1465, 3308, 1127, 2270, 182, 3674, 2831, 2318, 2716, 1776, 3368, 2981, 2986, 362, 561, 2228, 636, 830, 3216, 1947, 249, 3035, 1714, 3520, 1132, 3301, 1908, 2130, 3197, 2967, 2154, 1074, 1671, 2085, 3671, 813, 415, 2294, 613, 326, 1719, 923, 1505, 3445, 1256